In [ ]:
import pandas as pd
import numpy as np
import random
import networkx as nx
from tqdm import tqdm
import re
import matplotlib.pyplot as plt
import pickle

from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, roc_auc_score
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.metrics import precision_recall_curve
from matplotlib import pyplot
from sklearn.metrics import precision_recall_curve,roc_curve
from plot_metric.functions import BinaryClassification

df = pd.read_csv('genes_to_phenotype.txt', sep='\t',header=None)
df = df.loc[df[7] == "orphadata"]

df = df[[2,8]]
df.columns = ['HPO','GENE']
df = df.reset_index(drop=True)


In [ ]:
G = nx.from_pandas_edgelist(df, "HPO", "GENE", create_using=nx.Graph())


In [ ]:
#Degree distribution
def plot_degree_dist(G):
    degrees = [G.degree(n) for n in G.nodes()]
    plt.hist(degrees,bins=100,range=(0,50),color='green')
    plt.title("Degree Distribution")
    plt.ylabel("Count")
    plt.xlabel("Degree")
    plt.show()

plot_degree_dist(G)


In [ ]:
print("Total no. of Edge:", G.number_of_edges())
print("Total no. of Nodes:", G.number_of_nodes())
print("Size of the largest connected component in the graph:",len(max(nx.connected_components(G), key=len)))
print("Clustering Coefficient:",nx.average_clustering(G))


In [ ]:
# plot graph
plt.figure(figsize=(10,10))
pos = nx.random_layout(G, seed=23)
nx.draw(G, with_labels=False,  pos = pos, node_size = 5, alpha = 0.6, width = 0.7)

plt.show()


## Dataset Preparation for Model Building
We need to prepare the dataset from an undirected graph. 
This dataset will have features of node pairs and the target variable would be binary in nature, indicating the presence of links (or not).

### Retrieve Unconnected Node Pairs – Negative Samples

We have already understood that to solve a link prediction problem, we have to prepare a dataset from the given graph. A major part of this dataset is the negative samples or the unconnected node pairs. In this section, I will show you how we can extract the unconnected node pairs from a graph.

First, we will create an adjacency matrix to find which pairs of nodes are not connected.

For example, the adjacency of the graph below is a square matrix in which the rows and columns are represented by the nodes of the graph:

![title](img/img_1.png)


The links are denoted by the values in the matrix. 1 means there is a link between the node pair and 0 means there is a link between the node pair. For instance, nodes 1 and 3 have 0 at their cross-junction in the matrix and these nodes also have no edge in the graph above.

We will use this property of the adjacency matrix to find all the unconnected node pairs from the original graph G:



In [ ]:
# combine all nodes in a list
node_list = df.HPO.tolist() + df.GENE.tolist()

# remove duplicate items from the list
node_list = list(dict.fromkeys(node_list))

# build adjacency matrix
adj_G = nx.to_numpy_matrix(G, nodelist = node_list)

In [ ]:
range(adj_G.shape[0])

As you can see, it is a square matrix. Now, we will traverse the adjacency matrix to find the positions of the zeros. Please note that we don’t have to go through the entire matrix. The values in the matrix are the same above and below the diagonal, as you can see below:

![title](img/img_2.png)


We can either search through the values above the diagonal (green part) or the values below (red part). Let’s search the diagonal values for zero:


In [ ]:

# # get unconnected node-pairs
# all_unconnected_pairs = []

# # traverse adjacency matrix
# offset = 0
# for i in tqdm(range(adj_G.shape[0])):
#   for j in range(offset,adj_G.shape[1]):
#     if node_list[i] != node_list[j]:
#       try:
#           val = nx.shortest_path_length(G, node_list[i],node_list[j])
#       except:
#           all_unconnected_pairs.append([node_list[i],node_list[j]])
#       if val <=2 :
#         if adj_G[i,j] == 0:
#           all_unconnected_pairs.append([node_list[i],node_list[j]])

#   offset = offset + 1

# with open("all_unconnected_pairs_orpha.txt", "wb") as fp:   #Pickling
#     pickle.dump(all_unconnected_pairs, fp)

In [ ]:
# all_unconnected_pairs = []
# import ast
# with open("all_unconnected_pairs_orpha.txt", "r") as f:
#   for line in f:
#     x = ast.literal_eval(line.strip())
#     all_unconnected_pairs.append(x)
    #print(all_unconnected_pairs)

In [ ]:
with open("all_unconnected_pairs_orpha_pkl.txt", "rb") as fp:   # Unpickling
    all_unconnected_pairs = pickle.load(fp)

We have 19,018 unconnected pairs. These node pairs will act as negative samples during the training of the link prediction model. Let’s keep these pairs in a dataframe:

In [ ]:
node_1_unlinked = [i[0] for i in all_unconnected_pairs]
node_2_unlinked = [i[1] for i in all_unconnected_pairs]

data = pd.DataFrame({'HPO':node_1_unlinked, 
                     'GENE':node_2_unlinked})

# add target variable 'link'
data['link'] = 0

Remove Links from Connected Node Pairs – Positive Samples

As we discussed above, we will randomly drop some of the edges from the graph. However, randomly removing edges may result in cutting off loosely connected nodes and fragments of the graph. This is something that we have to take care of. We have to make sure that in the process of dropping edges, all the nodes of the graph should remain connected.

In the code block below, we will first check if dropping a node pair results in the splitting of the graph (number_connected_components > 1) or reduction in the number of nodes. If both things do not happen, then we drop that node pair and repeat the same process with the next node pair.

Eventually, we will get a list of node pairs that can be dropped from the graph and all the nodes would still remain intact:

In [ ]:
# initial_node_count = len(G.nodes)

# df_temp = df.copy()

# # empty list to store removable links
# omissible_links_index = []

# for i in tqdm(df.index.values):
  
#   # remove a node pair and build a new graph
#   G_temp = nx.from_pandas_edgelist(df_temp.drop(index = i), "HPO", "GENE", create_using=nx.Graph())
#   # check there is no spliting of graph and number of nodes is same
#   if (nx.number_connected_components(G_temp) == 1) and (len(G_temp.nodes) == initial_node_count):
#     omissible_links_index.append(i)
#     df_temp = df_temp.drop(index = i)


# with open("omissible_links_index_orpha.txt", "w") as f:
#     for s in omissible_links_index:
#         f.write(str(s) +"\n") 

### Reading the saved omissible links index file

In [ ]:
omissible_links_index = []
with open("omissible_links_index_orpha.txt", "r") as f:
  for line in f:
    omissible_links_index.append(int(line.strip()))

In [ ]:
len(omissible_links_index)

We have over 125304 links that we can drop from the graph. These dropped edges will act as positive training examples during the link prediction model training.

 
### Data for Model Training

Next, we will append these removable edges to the dataframe of unconnected node pairs. Since these new edges are positive samples, they will have a target value of ‘1’:

In [ ]:
# create dataframe of removable edges
df_ghost = df.loc[omissible_links_index]

# add the target variable 'link'
df_ghost['link'] = 1

data = data.append(df_ghost, ignore_index=True)

### Let’s check the distribution of values of the target variable:

In [ ]:
data['link'].value_counts() #Total 1665146 ~7.5% incident rate

It turns out that this is highly imbalanced data. The ratio of link vs no link is just close to ~7.5%. In the next section, we will extract features for all these node pairs.


## Feature Extraction
We will use the node2vec algorithm to extract node features from the graph after dropping the links. So, let’s first create a new graph after dropping the removable links:

In [ ]:
# drop removable edges
df_partial = data.drop(index=df_ghost.index.values)

# build graph
G_data = nx.from_pandas_edgelist(df_partial, "HPO", "GENE", create_using=nx.Graph())

Next, we will install the `node2vec` library. It is quite similar to the `DeepWalk` algorithm. However, it involves biased random walks. To know more about node2vec, you should definitely check out this paper node2vec: Scalable Feature Learning for Networks.

For the time being, just keep in mind node2vec is used for vector representation of nodes of a graph. Let’s install it:

`pip install node2vec`

It might take a while to install on your local machine (it’s quite fast if you’re using Colab).

Now, we will train the `node2vec` model on our graph (G_data):


In [ ]:
from node2vec import Node2Vec

# Generate walks
node2vec = Node2Vec(G_data, dimensions=128, walk_length=30, num_walks=200, workers=1)

# train node2vec model
n2w_model = node2vec.fit(window=7, min_count=1)

## Save `node2vec` model

In [ ]:
# Save model for later use
n2w_model.save('node2vec.model')


## Load saved `node2vec` model

In [ ]:
from gensim.models import Word2Vec
n2w_model = Word2Vec.load("node2vec.model")

Next, we will apply the trained node2vec model on each and every node pair in the dataframe ‘data’. To compute the features of a pair or an edge, we will add up the features of the nodes in that pair:

In [ ]:
x = [(n2w_model.wv.get_vector(str(i)) + n2w_model.wv.get_vector(str(j))) for i,j in zip(data['HPO'], data['GENE'])]

## Building our Link Prediction Model
To validate the performance of our model, we should split our data into two parts – one for training the model and the other to test the model’s performance:



In [ ]:
xtrain, xtest, ytrain, ytest = train_test_split(np.array(x), data['link'], 
                                                test_size = 0.2, 
                                                random_state = 35)

### Logistic Regression
Let’s fit a logistic regression model first:

In [ ]:
lr = LogisticRegression(class_weight="balanced",verbose=1,solver='lbfgs',penalty='l2')
lr.fit(xtrain, ytrain)

We will now make predictions on the test set and We will use the AUC-ROC score to check our model’s performance. To learn more about this evaluation metric, you may check out this article: Important Model Evaluation Metrics for Machine Learning.

In [ ]:
from matplotlib import pyplot
from sklearn.metrics import precision_recall_curve,roc_curve
from plot_metric.functions import BinaryClassification

predictions = lr.predict_proba(xtest)
with open('logistic_regression_pred.pkl', 'wb') as f:
    pickle.dump(predictions[:,1].tolist(), f)



### AUC-ROC & AUC-PR Curve for Logistic Regression

In [ ]:
with open('logistic_regression_pred.pkl', 'rb') as f:
    lr_pred = pickle.load(f)

# Visualisation with plot_metric
bc = BinaryClassification(ytest, lr_pred, labels=["0", "1"])

# Figures
plt.figure(figsize=(5,5))
bc.plot_roc_curve()
plt.title('AUC-ROC for Logistic Regression')
plt.show()

In [ ]:
# Figures
plt.figure(figsize=(5,5))
bc.plot_precision_recall_curve()
plt.title('AUC-PR for Logistic Regression')
plt.show()

In [ ]:
from sklearn.metrics import average_precision_score

print(average_precision_score(ytest, lr_pred))

In [ ]:
bc.plot_class_distribution()

In [ ]:
print("             __________________________________________")
print("              Classification Report Deep Multilayer NN")
print("             ‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾")
bc.print_report()

In [ ]:
from sklearn.metrics import classification_report
t=.5
y_pred_class = [1 if y_i > t else 0 for y_i in lr_pred]

print("             __________________________________________")
print("              Classification Report Logistic Regression")
print("             ‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾")
print(classification_report(ytest, y_pred_class, target_names=["0", "1"]))

## Deep Neural Network

In [ ]:
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout

from keras.optimizers import Adam
from keras.initializers import Constant
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import StratifiedKFold
from sklearn.utils import class_weight
class_weights = class_weight.compute_class_weight('balanced',np.unique(ytrain),ytrain)
class_weights = dict(enumerate(class_weights))
#pos/total
output_bias = 0.075
# encode class values as integers
encoder = LabelEncoder()
encoder.fit(ytrain)
encoded_Y = encoder.transform(ytrain)
# baseline model
def create_baseline():
	# create model
	model = Sequential()
	model.add(Dense(128, input_dim=128, activation='relu',kernel_initializer='he_uniform'))
	model.add(Dense(1, activation='sigmoid',bias_initializer=Constant(output_bias)))
	# Compile model
	model.compile(loss='binary_crossentropy', optimizer=Adam(lr=1e-3))
	return model
# evaluate model with standardized dataset
estimator = KerasClassifier(build_fn=create_baseline, epochs=100 , verbose=1)
estimator.fit(xtrain,ytrain,class_weight=class_weights)
# kfold = StratifiedKFold(n_splits=5, shuffle=True)
# results = cross_val_score(estimator, xtrain, encoded_Y, cv=kfold)
# print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

In [ ]:
predictions = estimator.predict(xtest)
with open('nn_pred.pkl', 'wb') as f:
    pickle.dump(predictions.tolist(), f)

In [ ]:
with open('nn_pred.pkl', 'rb') as f:
    nn_pred = pickle.load(f)
roc_auc_score(ytest, nn_pred)

In [ ]:

# Visualisation with plot_metric
bc = BinaryClassification(ytest, nn_pred, labels=["0", "1"])

# Figures
plt.figure(figsize=(5,5))
bc.plot_roc_curve()
plt.title('AUC-ROC for Deep Multilayer NN')
plt.show()

In [ ]:
# Figures
plt.figure(figsize=(5,5))
bc.plot_precision_recall_curve()
plt.title('AUC-PR for Deep Multilayer NN')
plt.show()

In [ ]:
from sklearn.metrics import classification_report
t=.5
#y_pred_class = [1 if y_i > t else 0 for y_i in nn_pred]

print("             __________________________________________")
print("              Classification Report Deep Multilayer NN")
print("             ‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾")
print(classification_report(ytest, nn_pred, target_names=["0", "1"]))

In [ ]:
nn_pred

In [ ]:
#ROC Curve
from sklearn.metrics import roc_curve
from sklearn.metrics import confusion_matrix, precision_recall_curve, auc, roc_curve, average_precision_score



fpr1 , tpr1, thresholds1 = roc_curve(ytest, nn_pred)
roc_auc_1 = auc(fpr1, tpr1)

fpr2 , tpr2, thresholds2 = roc_curve(ytest, lr_pred)
roc_auc_5 = auc(fpr2, tpr2)


plt.plot([0,1],[0,1], 'k--')

plt.plot(fpr1, tpr1, label= 'Neural Network (area = %0.2f)' % roc_auc_1)
plt.plot(fpr2, tpr2, label= 'Logistic Regression (area = %0.2f)' % roc_auc_2)

plt.legend()
plt.xlabel("False Positive Rate (1 - Specificity)")
plt.ylabel("True Positive Rate")
plt.title('AUROC')
plt.show()

In [ ]:
#PR Curve
from sklearn.metrics import roc_curve
from sklearn.metrics import confusion_matrix, precision_recall_curve, auc, roc_curve, average_precision_score


fpr1 , tpr1, thresholds1 = precision_recall_curve(ytest, nn_pred)
roc_auc_1 = average_precision_score(ytest, nn_pred)

fpr2 , tpr2, thresholds2 = precision_recall_curve(ytest, lr_pred)
roc_auc_2 = average_precision_score(ytest, lr_pred)

no_skill = len(ytest[ytest==1]) / len(ytest)
pyplot.plot([0, 1], [0.01, 0.01], label='Baseline', color="black")

plt.plot(fpr1, tpr1, label= 'Neural Network ( %0.2f)' % roc_auc_1)
plt.plot(fpr2, tpr2, label= 'Logistic Regression (%0.2f)' % roc_auc_2, color='b')


plt.legend(loc = 'lower left')
plt.xlabel("Precision")
plt.ylabel("Recall")
plt.title('AUCPR')
plt.show()